# Orbital-Optimization for reducing the one-norm

Author : Dr. Saad Yalouz - MSc Emiel Koridon (Cool titles)

A starting point to minimize the One-norm using Orbital-Optimization and a gradient free optimizer

## Theory 
The idea here is to employ a unitary transformation to modify the MOs of the system in order to minimize the One-norm. To build up this unitary, we start by the definition of the Orbital rotation operator which reads
$$ U(\vec{\kappa}) =\sum_{t>u}^{active} \kappa_{tu} (\hat{E}_{tu} - \hat{E}_{ut})$$
with $\hat{E}_{tu}=\frac{1} {\sqrt{2}}\sum_{\sigma}a^\dagger_{t,\sigma} a_{u,\sigma}$ and $\kappa_{tu}$ a rotation parameter affecting MOs $t$ and $u$ (note the absence of self rotation here with $t\neq u$). This operator takes the form of single excitations (with $t,u$ indices running only in the active space). Starting from this definition, a little bit of aglebra can show that implementing this rotation operator on creation/anihilation operators is strictly equivalent to redefining the MO coeff matrix of the Hamiltonian as follows
$$ \mathbf{C}_{new}(\vec{\kappa}) = \mathbf{C}_{ref} \mathbf{U}_{OO}(\vec{\kappa}) $$ 
Here, $\mathbf{U}_{OO}(\vec{\kappa})$ is a matrix representation of the effect of the rotations operator on the MOs. This matrix is an exponentiated version of the skew-matrix noted $\mathbf{K}$ encoding the parameter $\vec{\kappa}$. In other words
$$\mathbf{U}_{OO}(\vec{\kappa}) = e^{-\mathbf{K}} \text{,  with  } \mathbf{K} = skew(\vec{\kappa}) = \pmatrix{ 0 & \kappa_{01} & \kappa_{02} & \ldots & \kappa_{0N} \\
-\kappa_{01} & 0 & \kappa_{12} & \ldots & \kappa_{1N} \\
-\kappa_{02} & -\kappa_{12} & 0 &\ldots & \vdots \\
\vdots & \vdots & \vdots &\ddots & \vdots \\
-\kappa_{0N} & -\kappa_{1N} & \ldots & \ldots & 0 }$$

## Numerical implementation

Starting from this, we can encode this exponential numerically and use the kappa parameters (total number of parameters = $N(N-1)/2$) as degrees of freedom to reduce the one-norm. For this, first I use scimpy symbols to encode the matrix.

In [72]:
import psi4
import sys
import os
import openfermion
from openfermionpyscf import run_pyscf, compute_integrals
import numpy as np
import copy
from scipy.optimize import minimize
import math as m
import scipy 
import sympy
from sympy.matrices import zeros
from random import random
from openfermion import ops, InteractionOperator, get_sparse_operator, jordan_wigner
from openfermion.functionals import JW1norm_spat
from pyscf import gto, scf, lo, tools, fci, ao2mo, mcscf, df
import module as md
import time

# Set molecule parameters.
basis = ['sto-3g', 'cc-pvdz','def2svp'][0]
multiplicity = 1

# Set calculation parameters.
consider_cas = 0 # Do we consider an active space or the full space?
# Set size of active space
n_orbitals = 8
n_electrons = 8
# Choose whether you want to start from localized orbitals or canonical orbitals
localize = 1
# Choose whether you want to start with a random initial rotation
randomize = 0
# Import .xyz geometry. This is kind of an involved code because I have many different geometries available...
# If you want to consider a Hydrogen chain or ring, set the following to 1
H_chain = 0
H_ring = 0
run_fci = 0
run_casci = 0
if H_chain:
    N_atoms = 12
    r = 1.8
    if consider_cas:
        description = 'H' + str(N_atoms) + str(basis) + 'ne' + str(n_electrons) +\
            'no' + str(n_orbitals)
    else:
        description = 'H' + str(N_atoms) + str(basis)
    geometry = [('H',( 0., 0., z*r)) for z in range(N_atoms)]
    
elif H_ring:
    theta = 88 * np.pi/180
    r = 1.3
    # Introduction of the molecular structure (.txt file)
    geometry = [
                ('H', (r*np.cos(theta/2.),   r*np.sin(theta/2.),  0.)),
                ('H', (r*np.cos(theta/2.),   -r*np.sin(theta/2.), 0.)),
                ('H', (-r*np.cos(theta/2.),  r*np.sin(theta/2.),  0.)),
                ('H', (-r*np.cos(theta/2.),  -r*np.sin(theta/2.), 0.))
                ]
    if consider_cas:
        description = 'H4' + str(basis) + 'ne' + str(n_electrons) + 'no' + str(n_orbitals)
    else:
        description = 'H4' + str(basis)

else:
    fname = ['xyz_files/H2nosym.txt','xyz_files/H2COnosym.txt','xyz_files/H10.txt',\
             'xyz_files/C2.txt', 'xyz_files/LiH.txt', 'xyz_files/HLiO.txt', \
             'xyz_files/H2Onosym.txt', 'xyz_files/H14.txt', \
             'xyz_files/hnch2_s0min_dzp.txt', 'xyz_files/hnc3h6_s0min_dzp.txt',\
             'xyz_files/hnc5h10_s0min_dzp.txt', 'xyz_files/hnc7h14_s0min_dzp.txt',\
             'xyz_files/benzene.txt','xyz_files/PCy3.txt','xyz_files/PCy3Cl2Ru.txt',\
             'xyz_files/femoco.txt', 'xyz_files/M06-L.txt','xyz_files/butane.txt',\
             'xyz_files/pentane.txt','xyz_files/hexane.txt','xyz_files/heptane.txt',\
             'xyz_files/butene.txt','xyz_files/pentene.txt','xyz_files/hexene.txt',\
             'xyz_files/heptene.txt'][-4]
    geometry = md.xyz_to_geom(fname)
    if consider_cas:
        description = fname.replace('xyz_files/','').replace('.txt','') + str(basis)\
            + 'ne' + str(n_electrons) + 'no' + str(n_orbitals)
    else:
        description = fname.replace('xyz_files/','').replace('.txt','') + str(basis)

# Determine number of AOs and electrons
nao = md.count_ao(geometry,basis,spin=multiplicity-1)
nelec = md.count_elec(geometry,basis,spin=multiplicity-1)
nmo = nao
print('nao:',nao,'\nnelec:', nelec)
threshold = 1e-10

# Set active indices
if consider_cas:
    ncore = (nelec - n_electrons) // 2
    ntot = ncore + n_orbitals # Number of core orbitals + number of active orbitals
    active_indices = list(range(ncore,ntot))
    occupied_indices = list(range(ncore))
else:
    ncore = 0
    ntot = nmo
    active_indices = list(range(nmo))
    occupied_indices = []

print(active_indices,occupied_indices)
# Build molecule and run RHF
mol = gto.Mole()
mol.atom = geometry
mol.basis = basis
mol.spin = multiplicity - 1
mol.symmetry = 0
mol.build()

if multiplicity == 1:
    myhf = scf.RHF(mol)
else:
    myhf = scf.ROHF(mol)

myhf.run()

# Extract MO_coeff and integrals. Then determine qubit 1-norm for CMOs and Pipek-Mezey MOs.

C_nonloc = np.copy(myhf.mo_coeff)

constant = float(mol.energy_nuc())


print('---------NON-LOCALIZED_ORBITALS---------')

C_copy = np.copy(C_nonloc)
t8 = time.time()
one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_copy[:,:ntot], threshold)
print("calculating integrals took",time.time()-t8)

if consider_cas:
    t10 = time.time()
    CASconstant, one_body_integrals, two_body_integrals =\
    md.get_active_space_integrals(one_body_integrals,
                                  two_body_integrals,
                                  occupied_indices,
                                  active_indices)
    print("transforming integrals to active space ints took", time.time()-t10)
else:
    CASconstant = 0
t4 = time.time()
qub1norm = JW1norm_spat(np.copy(constant+CASconstant),
                        np.copy(one_body_integrals),
                        np.copy(two_body_integrals))
print('\ncalculating norm of qubit hamiltonian took', time.time()-t4)

print('\n')

print('---------LOCALIZED_ORBITALS---------')
localizemethod = ['Pipek-Mezey','Boys','ibo','ER'][1]

C = np.copy(C_nonloc)
if localizemethod == 'Pipek-Mezey':
    orb = lo.PipekMezey(mol).kernel(C[:,ncore:ntot])
elif localizemethod == 'Boys':
    orb = lo.Boys(mol).kernel(C[:,ncore:ntot])
elif localizemethod == 'ibo':
    orb = lo.ibo.ibo(mol, C[:,ncore:ntot])
elif localizemethod == 'ER':
    orb = lo.EdmistonRuedenberg(mol).kernel(C[:,ncore:ntot])
else:
    raise ValueError('Localization method not recognized')

C_locPM = np.hstack((C_nonloc[:,:ncore],orb,C_nonloc[:,ntot:nmo]))
one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_locPM[:,:ntot], threshold)
if consider_cas:
    CASconstant_PM, one_body_integrals, two_body_integrals =\
    md.get_active_space_integrals(one_body_integrals,
                                  two_body_integrals,
                                  occupied_indices,
                                  active_indices)
else:
    CASconstant_PM = 0
t4 = time.time()
qub1norm_locPM = JW1norm_spat(np.copy(constant+CASconstant_PM),
                        np.copy(one_body_integrals),
                        np.copy(two_body_integrals))
print('calculating norm of qubit hamiltonian took', time.time()-t4)

if consider_cas:
    print("Considering 1-norm of active space Hamiltonian")
else:
    print("Considering 1-norm of full space Hamiltonian")
    
print("starting 1-norm nonloc is:",qub1norm)
print("1norm locPM is:",qub1norm_locPM)


OPT_OO_MAX_ITER  = 5000 # Maximum number of steps for the OO

# Building the K matrix : generator for the MO rotations 
Rot_param_values = []
Rot_param_names  = []
bounds = (-1.,1.)

K_mat_sym = zeros( nmo )
bounds = []
for q in range(nmo-1):
    for p in range(q+1,nmo):
        if ( p in active_indices and q in active_indices ) or ( p in occupied indices and q in occupied_indices):
            K_mat_sym[ p, q ] = - sympy.Symbol( "K_{}{}".format( p, q ) )
            K_mat_sym[ q, p ] = - K_mat_sym[ p, q ] 
            Rot_param_names  += [sympy.Symbol( "K_{}{}".format( p, q ))]
            Rot_param_values += [1e-1 * (random()-0.5) if randomize else 0.] # <== Set starting Rot_param_values here.
            bounds += [ [-1., 1.] ] 

# Building the bounds for the rotational parameter amplitudes in the form of constraints
# (simply beacause cobyla doesn't have intrinsic bound options)
cons = []
for factor in range(len(bounds)):
    lower, upper = bounds[factor]
    l = {'type': 'ineq',
         'fun': lambda x, lb=lower, i=factor: x[i] - lb}
    u = {'type': 'ineq',
         'fun': lambda x, ub=upper, i=factor: ub - x[i]}
    cons.append(l)
    cons.append(u)


nao: 26 
nelec: 30
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25] []
converged SCF energy = -153.016760492909
---------NON-LOCALIZED_ORBITALS---------
calculating integrals took 0.12904644012451172

calculating norm of qubit hamiltonian took 0.31020426750183105


---------LOCALIZED_ORBITALS---------
calculating norm of qubit hamiltonian took 0.29170823097229004
Considering 1-norm of full space Hamiltonian
starting 1-norm nonloc is: 676.4915812479691
1norm locPM is: 396.1348564758652


In [73]:
print(CASconstant, CASconstant_PM, constant)
print(active_indices)
print(occupied_indices)
print(ncore,ntot)
print(Rot_param_values)

0 0 103.8557090281905
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25]
[]
0 26
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0,

In [74]:
K      = np.array( K_mat_sym.subs(list(zip(Rot_param_names,Rot_param_values))) ).astype(np.float64)  
U_OO   = scipy.linalg.expm( - K )
print(U_OO)
print("check if U_OO is unitary:",np.allclose(np.eye(U_OO.shape[0]), U_OO @ U_OO.T))

[[1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0.]
 [0.

Then I define a cost function to encode the evaluation of the One-Norm using the new MO coeff matrix. In the latter, we compute the 1-norm from the integrals. To proceed, we use $\mathbf{C}_{new}(\vec{\kappa})$ to build up the new electronic integrals.

In [ ]:
def K_matr(Rot_param_values, active_indices):
    K = zeros( nmo )
    n = 0
    for q in range(nmo-1):
        for p in range(q+1,nmo):
            if ( p in active_indices and q in active_indices ):
                K[ p, q ] = - Rot_param_values[n]
                K[ q, p ] = - K[ p, q ]
                n += 1
    return np.array(K)

def Cost_function_OO_OneNorm(Rot_param_values):
    """
    Cost function to minimize the One-Norm using MO rotations.
    """
    t6 = time.time()
    t5 = time.time()
    K = K_matr(Rot_param_values, active_indices)
    print("\nInitializing K-matrix took:",time.time()-t5)
    t1 = time.time()
    U_OO   = scipy.linalg.expm( - K )
    print("exponentiating matrix took:",time.time()-t1)
    t3 = time.time()
    if localize:
        C_MO   = C_locPM @ U_OO
    else:
        C_MO   = C_nonloc @ U_OO
    print("Matrix multiplication took:",time.time()-t3)
    t2 = time.time()
    one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_MO[:,:ntot], threshold)
    print("extracting integrals took:",time.time()-t2)
    t4 = time.time()
    if consider_cas:
        CASconstant, one_body_integrals, two_body_integrals =\
        md.get_active_space_integrals(one_body_integrals,
                                      two_body_integrals,
                                      occupied_indices,
                                      active_indices)
    else:
        CASconstant = 0
    t4 = time.time()
    OneNorm = JW1norm_spat(np.copy(constant+CASconstant),
                           np.copy(one_body_integrals),
                           np.copy(two_body_integrals))
    print('calculating norm of qubit hamiltonian took', time.time()-t4)
    print('1-norm is:',OneNorm)
    print("total time for 1 cost function evaluation is", time.time()-t6)
    return OneNorm

print("starting 1-norm nonloc is:",qub1norm)
print("1norm locPM is:",qub1norm_locPM)
t7 = time.time()
f_min_OO = minimize( Cost_function_OO_OneNorm,
                      x0      = Rot_param_values,
                      constraints=cons,
                      method  = 'cobyla',
                      options = {'maxiter': OPT_OO_MAX_ITER,
                                'tol'    : 1e-5,
                                'disp': True}  )
print("total time for minimization with",OPT_OO_MAX_ITER,"max iterations was:", time.time()-t7)

starting 1-norm nonloc is: 676.4915812479691
1norm locPM is: 396.1348564758652

Initializing K-matrix took: 0.0211026668548584
exponentiating matrix took: 0.00234222412109375
Matrix multiplication took: 0.00020241737365722656
extracting integrals took: 0.12246084213256836
calculating norm of qubit hamiltonian took 0.3097257614135742
1-norm is: 396.1348564758652
total time for 1 cost function evaluation is 0.45621228218078613

Initializing K-matrix took: 0.01570439338684082
exponentiating matrix took: 0.0011723041534423828
Matrix multiplication took: 6.771087646484375e-05
extracting integrals took: 0.1178741455078125
calculating norm of qubit hamiltonian took 0.29898500442504883
1-norm is: 413.10761436332467
total time for 1 cost function evaluation is 0.43453168869018555

Initializing K-matrix took: 0.015433788299560547
exponentiating matrix took: 0.0017657279968261719
Matrix multiplication took: 8.7738037109375e-05
extracting integrals took: 0.11695384979248047
calculating norm of qub

calculating norm of qubit hamiltonian took 0.3024730682373047
1-norm is: 424.0927134708394
total time for 1 cost function evaluation is 0.4364786148071289

Initializing K-matrix took: 0.027980327606201172
exponentiating matrix took: 0.0018732547760009766
Matrix multiplication took: 0.0001342296600341797
extracting integrals took: 0.12374591827392578
calculating norm of qubit hamiltonian took 0.3045501708984375
1-norm is: 410.491469084692
total time for 1 cost function evaluation is 0.45893120765686035

Initializing K-matrix took: 0.015943050384521484
exponentiating matrix took: 0.0014617443084716797
Matrix multiplication took: 5.698204040527344e-05
extracting integrals took: 0.12275242805480957
calculating norm of qubit hamiltonian took 0.28753232955932617
1-norm is: 412.0514414931579
total time for 1 cost function evaluation is 0.42811131477355957

Initializing K-matrix took: 0.01575326919555664
exponentiating matrix took: 0.001222372055053711
Matrix multiplication took: 0.00013375282

calculating norm of qubit hamiltonian took 0.29445791244506836
1-norm is: 418.8210729593152
total time for 1 cost function evaluation is 0.4279184341430664

Initializing K-matrix took: 0.016322612762451172
exponentiating matrix took: 0.0014235973358154297
Matrix multiplication took: 0.00017595291137695312
extracting integrals took: 0.11903786659240723
calculating norm of qubit hamiltonian took 0.3027379512786865
1-norm is: 422.61296815385214
total time for 1 cost function evaluation is 0.4402439594268799

Initializing K-matrix took: 0.015648365020751953
exponentiating matrix took: 0.0016605854034423828
Matrix multiplication took: 6.4849853515625e-05
extracting integrals took: 0.11615896224975586
calculating norm of qubit hamiltonian took 0.2886631488800049
1-norm is: 421.4383800121841
total time for 1 cost function evaluation is 0.4226226806640625

Initializing K-matrix took: 0.015658855438232422
exponentiating matrix took: 0.001216888427734375
Matrix multiplication took: 0.00013327598

calculating norm of qubit hamiltonian took 0.29605841636657715
1-norm is: 425.17017879973264
total time for 1 cost function evaluation is 0.4343106746673584

Initializing K-matrix took: 0.015737056732177734
exponentiating matrix took: 0.0011970996856689453
Matrix multiplication took: 0.00010442733764648438
extracting integrals took: 0.11669445037841797
calculating norm of qubit hamiltonian took 0.297576904296875
1-norm is: 425.08195421335574
total time for 1 cost function evaluation is 0.43155741691589355

Initializing K-matrix took: 0.015533208847045898
exponentiating matrix took: 0.0012385845184326172
Matrix multiplication took: 5.6743621826171875e-05
extracting integrals took: 0.11478400230407715
calculating norm of qubit hamiltonian took 0.29210591316223145
1-norm is: 427.21123458131603
total time for 1 cost function evaluation is 0.4239461421966553

Initializing K-matrix took: 0.015015125274658203
exponentiating matrix took: 0.0012254714965820312
Matrix multiplication took: 8.7499

calculating norm of qubit hamiltonian took 0.3118250370025635
1-norm is: 414.70369326090736
total time for 1 cost function evaluation is 0.4473450183868408

Initializing K-matrix took: 0.01535654067993164
exponentiating matrix took: 0.0010981559753417969
Matrix multiplication took: 8.606910705566406e-05
extracting integrals took: 0.11681342124938965
calculating norm of qubit hamiltonian took 0.30163145065307617
1-norm is: 414.43453486517654
total time for 1 cost function evaluation is 0.43526554107666016

Initializing K-matrix took: 0.016129493713378906
exponentiating matrix took: 0.0010826587677001953
Matrix multiplication took: 7.414817810058594e-05
extracting integrals took: 0.11691403388977051
calculating norm of qubit hamiltonian took 0.29087185859680176
1-norm is: 409.8446873965334
total time for 1 cost function evaluation is 0.42581892013549805

Initializing K-matrix took: 0.015448331832885742
exponentiating matrix took: 0.0012061595916748047
Matrix multiplication took: 0.000131

...

extracting integrals took: 0.12006020545959473
calculating norm of qubit hamiltonian took 0.31488037109375
1-norm is: 371.4149750985829
total time for 1 cost function evaluation is 0.4616432189941406

Initializing K-matrix took: 0.025637149810791016
exponentiating matrix took: 0.003398895263671875
Matrix multiplication took: 0.00013971328735351562
extracting integrals took: 0.11896896362304688
calculating norm of qubit hamiltonian took 0.31694674491882324
1-norm is: 371.41359467362554
total time for 1 cost function evaluation is 0.46576881408691406

Initializing K-matrix took: 0.020836353302001953
exponentiating matrix took: 0.003387451171875
Matrix multiplication took: 0.00018095970153808594
extracting integrals took: 0.1189734935760498
calculating norm of qubit hamiltonian took 0.31029295921325684
1-norm is: 371.4143858730202
total time for 1 cost function evaluation is 0.45421624183654785

Initializing K-matrix took: 0.020609140396118164
exponentiating matrix took: 0.003377676010131

extracting integrals took: 0.119110107421875
calculating norm of qubit hamiltonian took 0.2969534397125244
1-norm is: 371.4184690183282
total time for 1 cost function evaluation is 0.43967294692993164

Initializing K-matrix took: 0.020652294158935547
exponentiating matrix took: 0.0034155845642089844
Matrix multiplication took: 0.0001380443572998047
extracting integrals took: 0.12087249755859375
calculating norm of qubit hamiltonian took 0.31596899032592773
1-norm is: 371.41530849357736
total time for 1 cost function evaluation is 0.4616382122039795

Initializing K-matrix took: 0.020963430404663086
exponentiating matrix took: 0.0034792423248291016
Matrix multiplication took: 0.0001316070556640625
extracting integrals took: 0.12002229690551758
calculating norm of qubit hamiltonian took 0.30341267585754395
1-norm is: 371.4146056005473
total time for 1 cost function evaluation is 0.4482753276824951

Initializing K-matrix took: 0.020207881927490234
exponentiating matrix took: 0.003166437149

calculating norm of qubit hamiltonian took 0.29602932929992676
1-norm is: 371.41476413701736
total time for 1 cost function evaluation is 0.44437217712402344

Initializing K-matrix took: 0.020193099975585938
exponentiating matrix took: 0.0036721229553222656
Matrix multiplication took: 1.0728836059570312e-05
extracting integrals took: 0.12763237953186035
calculating norm of qubit hamiltonian took 0.31871891021728516
1-norm is: 371.41002290667234
total time for 1 cost function evaluation is 0.47109150886535645

Initializing K-matrix took: 0.02282238006591797
exponentiating matrix took: 0.00436854362487793
Matrix multiplication took: 0.0001494884490966797
extracting integrals took: 0.1303715705871582
calculating norm of qubit hamiltonian took 0.3031938076019287
1-norm is: 371.4169262337592
total time for 1 cost function evaluation is 0.46141505241394043

Initializing K-matrix took: 0.022783279418945312
exponentiating matrix took: 0.004154205322265625
Matrix multiplication took: 1.16825103

calculating norm of qubit hamiltonian took 0.3047983646392822
1-norm is: 371.40566303487543
total time for 1 cost function evaluation is 0.4447016716003418

Initializing K-matrix took: 0.01932501792907715
exponentiating matrix took: 0.0033872127532958984
Matrix multiplication took: 0.0001404285430908203
extracting integrals took: 0.12037062644958496
calculating norm of qubit hamiltonian took 0.3001515865325928
1-norm is: 371.40546919663814
total time for 1 cost function evaluation is 0.4441072940826416

Initializing K-matrix took: 0.019388198852539062
exponentiating matrix took: 0.0033750534057617188
Matrix multiplication took: 0.00014400482177734375
extracting integrals took: 0.1180267333984375
calculating norm of qubit hamiltonian took 0.3037683963775635
1-norm is: 371.4088103064706
total time for 1 cost function evaluation is 0.44537997245788574

Initializing K-matrix took: 0.019681215286254883
exponentiating matrix took: 0.0031723976135253906
Matrix multiplication took: 0.000201463

calculating norm of qubit hamiltonian took 0.3005850315093994
1-norm is: 371.4073446731852
total time for 1 cost function evaluation is 0.4433019161224365

Initializing K-matrix took: 0.020053386688232422
exponentiating matrix took: 0.003493070602416992
Matrix multiplication took: 0.0001437664031982422
extracting integrals took: 0.11650419235229492
calculating norm of qubit hamiltonian took 0.3050191402435303
1-norm is: 371.40773379374576
total time for 1 cost function evaluation is 0.44591856002807617

Initializing K-matrix took: 0.020603179931640625
exponentiating matrix took: 0.003290891647338867
Matrix multiplication took: 0.00016021728515625
extracting integrals took: 0.12079906463623047
calculating norm of qubit hamiltonian took 0.29747438430786133
1-norm is: 371.4032961407979
total time for 1 cost function evaluation is 0.4428374767303467

Initializing K-matrix took: 0.020279645919799805
exponentiating matrix took: 0.0034554004669189453
Matrix multiplication took: 1.049041748046

In [ ]:
print("message:",f_min_OO.message,"number of function evaluations:",f_min_OO.nfev)

In [ ]:
K = K_matr(f_min_OO.x, active_indices)
U_OO   = scipy.linalg.expm( - K )
if localize:
    C_OO = C_locPM @ U_OO
else:
    C_OO = C_nonloc @ U_OO

one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_OO[:,:ntot], threshold)
if consider_cas:
        CASconstant, one_body_integrals, two_body_integrals =\
        md.get_active_space_integrals(one_body_integrals,
                                      two_body_integrals,
                                      occupied_indices,
                                      active_indices)
else:
        CASconstant = 0
OneNormorbOO = JW1norm_spat(np.copy(constant+CASconstant),
                            np.copy(one_body_integrals),
                            np.copy(two_body_integrals))

one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_nonloc[:,:ntot], threshold)
if consider_cas:
        CASconstant, one_body_integrals, two_body_integrals =\
        md.get_active_space_integrals(one_body_integrals,
                                      two_body_integrals,
                                      occupied_indices,
                                      active_indices)
else:
        CASconstant = 0
OneNormorbnonloc = JW1norm_spat(np.copy(constant+CASconstant),
                                np.copy(one_body_integrals),
                                np.copy(two_body_integrals))

one_body_integrals, two_body_integrals = compute_integrals(
        mol, myhf, C_locPM[:,:ntot], threshold)
if consider_cas:
        CASconstant, one_body_integrals, two_body_integrals =\
        md.get_active_space_integrals(one_body_integrals,
                                      two_body_integrals,
                                      occupied_indices,
                                      active_indices)
else:
        CASconstant = 0
OneNormorblocPM = JW1norm_spat(np.copy(constant+CASconstant),
                       np.copy(one_body_integrals),
                       np.copy(two_body_integrals))
if randomize:
    print("Starting from random orbital rotation...")
if consider_cas:
    print("Considering CAS(" + str(n_electrons) + "," + str(n_orbitals) + "), \n1norm of CMO orb is",
         OneNormorbnonloc, "\n1norm of PM orb is", OneNormorblocPM, "\n1norm of optimizer is", OneNormorbOO)
else:
    print("Considering full space, \n1norm of CMO orb is",
         OneNormorbnonloc, "\n1norm of PM orb is", OneNormorblocPM, "\n1norm of optimizer is", OneNormorbOO)

## Visualize
If you want to save the orbitals to gaussian CUBE files

In [55]:
Cost_function_OO_OneNorm(f_min_OO.x)
K = K_matr(f_min_OO.x, active_indices)
U_OO   = scipy.linalg.expm( - K )
if localize:
    C_OO = C_locPM @ U_OO
else:
    C_OO = C_nonloc @ U_OO
t13 = time.time()
for i in range(ncore,ntot):
    tools.cubegen.orbital(mol, os.getcwd() + '/CUBE_FILES/pyscfcube'\
                          + description + 'onenorm_orb' + localizemethod + str(localize)\
                          + str(randomize) + str(consider_cas) + str(i) , C_OO[:,i])
print('Cube files of molecule', description,'created in', os.getcwd() + '/CUBE_FILES/')
print('extracting cube files took', time.time()-t13)


Initializing K-matrix took: 0.008901119232177734
exponentiating matrix took: 0.0016748905181884766
Matrix multiplication took: 0.0001659393310546875
extracting integrals took: 0.11084532737731934
calculating norm of qubit hamiltonian took 0.0030660629272460938
1-norm is: 164.77251538860583
total time for 1 cost function evaluation is 0.1260061264038086
Cube files of molecule butenesto-3gne8no8 created in /home/emielkoridon/1-Norm_calculations/CUBE_FILES/
extracting cube files took 3.2489850521087646


In [56]:
t13 = time.time()
for i in range(ncore,ntot):
    tools.cubegen.orbital(mol, os.getcwd() + '/CUBE_FILES/pyscfcube'\
                          + description + localizemethod + str(0)\
                          + str(randomize) + str(consider_cas) + str(i) , C_nonloc[:,i])
print('Cube files of molecule', description,'created in', os.getcwd() + '/CUBE_FILES/')
print('extracting cube files took', time.time()-t13)

Cube files of molecule butenesto-3gne8no8 created in /home/emielkoridon/1-Norm_calculations/CUBE_FILES/
extracting cube files took 3.2374775409698486


In [49]:
t13 = time.time()
for i in range(ncore,ntot):
    tools.cubegen.orbital(mol, os.getcwd() + '/CUBE_FILES/pyscfcube'\
                          + description + localizemethod + str(1)\
                          + str(randomize) + str(consider_cas) + str(i) , C_locPM[:,i])
print('Cube files of molecule', description,'created in', os.getcwd() + '/CUBE_FILES/')
print('extracting cube files took', time.time()-t13)

Cube files of molecule butenesto-3gne4no4 created in /home/emielkoridon/1-Norm_calculations/CUBE_FILES/
extracting cube files took 1.633298635482788


In [17]:
from openfermionpyscf import run_pyscf
from openfermion import MolecularData
from openfermion.transforms import jordan_wigner
molecule = MolecularData(
    geometry, basis, multiplicity,
    description=description)
t0 = time.time()
localize_sep = 0
do_svd = 0
also_h1e = 0
do_cholesky = 0
Orth_AO = 0
run_scf = 1
run_mp2 = 0
run_cisd = 0
run_ccsd = 0
run_fci = 0
run_casci = 0
# delete_input = True
# delete_output = True
save_tohdf5 = 0
max_memory = 8000
verbose = 1
visualize = 0
localize = 1
localize_virt = 1
localize_cas = 1
only_cas = 0
# Run pyscf.
molecule = run_pyscf(molecule,
                      threshold=threshold,
                      also_h1e=also_h1e,
                      run_scf=run_scf,
                      run_mp2=run_mp2,
                      run_cisd=run_cisd,
                      run_ccsd=run_ccsd,
                      run_fci=run_fci,
                      run_casci=run_casci,
                      n_electrons=n_electrons,
                      n_orbitals=n_orbitals,
                      verbose=verbose,
                      localize=localize,
                      visualize=visualize,
                      localizemethod=localizemethod,
                      localize_virt=localize_virt,
                      localize_cas=localize_cas,
                      only_cas=only_cas,
                      localize_sep=localize_sep,
                      do_cholesky=do_cholesky,
                      do_svd=do_svd,
                      Orth_AO=Orth_AO,
                      save_tohdf5=save_tohdf5,
                      max_memory=max_memory)
print('run_pyscf took', time.time() - t0)
molecular_hamiltonian = molecule.get_molecular_hamiltonian(occupied_indices,active_indices)
print(jordan_wigner(molecular_hamiltonian).induced_norm())

Doing HF took 0.13610291481018066
LOCALIZING TOGETHER n_core 10 n_active 14 n_virtual 6
core 10 ndocc 17 n_orb 14 nmo 30
localizing took 0.9336483478546143
Hartree-Fock energy for H10-C4_sto-3g_singlet_butanesto-3gne14no14 (34 electrons) is -155.4605346318745.
populating data fields in molecule class took 6.9141387939453125e-06
computing integrals and storing them took 0.224808931350708
saving data to molecular data structure took 1.52587890625e-05
run_pyscf took 1.3660013675689697
222.9027541914615
